From [a discussion](http://thread.gmane.org/gmane.comp.lang.perl.pdl.general/8667/focus=8669) on `pdl-general` on how to analyse a thin-layer chromatography image.

In [1]:
use Modern::Perl;
use PDL;
use PDL::Image2D;
use PDL::Graphics::LUT;
use PDL::ImageRGB;
use File::Temp;
use Data::Frame;
use List::AllUtils;

IPerl->helper( pdl_as_png => sub {
    my ($self, $pdl, @opts) = @_;
    my $tmp = File::Temp->new( SUFFIX => '.png' );
    $pdl->wim( $tmp->filename );
    my $png_displayable = IPerl->png( $tmp->filename, @opts );
    $png_displayable->iperl_data_representations; # make sure to build from filename
    $png_displayable;
});

my $tlc_img = rpic('TLC_arg.jpg');
IPerl->pdl_as_png( $tlc_img, height => 100 );

In [2]:
my $grey_img = $tlc_img->float->rgbtogr; # 0 - 255 greyscale
IPerl->pdl_as_png( $grey_img, height => 100 );

In [3]:
my $bin_img = $grey_img < 255/2; # simple thresholding
# black : background, white: foreground
IPerl->pdl_as_png( $bin_img, height => 100 );

In [4]:
my $cc_img = $bin_img->cc8compt; # connected component labelling
say $cc_img->info;

my @range = $cc_img->minmax;
my ($xvals, $count) = hist($cc_img, $range[0], $range[1]+1,1 );
$xvals -= 1/2; # bin centers are halfway between labels
my $counts_df = Data::Frame->new( columns => [ label => $xvals, count => $count ] );
say $counts_df;

PDL: Float D [2627,488]
---------------------
      label  count   
---------------------
 0    0      1215553 
 1    1      4839    
 2    2      4384    
 3    3      2389    
 4    4      2       
 5    5      1       
 6    6      3       
 7    7      1       
 8    8      30      
 9    9      2968    
 10   10     1       
 11   11     1       
 12   12     1       
 13   13     7329    
 14   14     1       
 15   15     5       
 16   16     1       
 17   17     2       
 18   18     5       
 19   19     8890    
 20   20     1       
 21   21     1       
 22   22     1       
 23   23     1       
 24   24     3       
 25   25     10      
 26   26     1       
 27   27     1       
 28   28     1       
 29   29     2       
 30   30     1       
 31   31     1       
 32   32     2       
 33   33     1       
 34   34     7       
 35   35     1       
 36   36     7       
 37   37     3       
 38   38     1       
 39   39     1       
 40   40     1       
 41   41

1


In [5]:
my $lut = pdl( ( lut_data('heat') )[0..2] )->xchg(0,1) * 256;
my $cc_img_label_colour = $cc_img->interlrgb( $lut )->long;
IPerl->pdl_as_png( $cc_img_label_colour, height => 100 );